In [1]:
import psycopg2
import json
from lst_servers import *
from tqdm import tqdm

# Parámetros de conexión a la base de datos

json_file_path = "./GeoJSON - Censo 2010 (Localidad) ITER.json"

with open(json_file_path, 'r', encoding='utf-8-sig') as f:
    json_content = json.load(f)

# Divide los datos en bloques más pequeños
chunk_size = 100  # Ajusta el tamaño del bloque según tus necesidades
json_features = json_content['features']

chunks = [json_features[i:i + chunk_size] for i in range(0, len(json_features), chunk_size)]

# Itera sobre los servidores e inserta los bloques de datos en la base de datos
for ip in l_ips:
    conn = psycopg2.connect(
        host=ip,
        port=5432,
        database="coordenadas_mx",
        user="postgres",
        password="Shala55951254"
    )
    
    cursor = conn.cursor()
    cursor.execute("DROP TABLE IF EXISTS coordenadas_loc;")

    create_table_query = """
    CREATE TABLE coordenadas_loc (
        key_edomunloc CHARACTER VARYING,
        id_edo CHARACTER VARYING,
        edo CHARACTER VARYING,
        id_mun CHARACTER VARYING, 
        mun CHARACTER VARYING,
        id_loc CHARACTER VARYING,
        loc CHARACTER VARYING,
        json_data JSONB
    );"""
    
    cursor.execute(create_table_query)
    
    # for i in tqdm(range(len(json_content['features']))):
    #     key_edomunloc = f"{json_content['features'][i]['properties']['entidad']}_{json_content['features'][i]['properties']['mun']}_{json_content['features'][i]['properties']['loc']}"
    #     id_edo = json_content['features'][i]['properties']['entidad']
    #     edo = json_content['features'][i]['properties']['nom_ent']
    #     id_mun = json_content['features'][i]['properties']['mun']
    #     mun = json_content['features'][i]['properties']['nom_mun']
    #     id_loc = json_content['features'][i]['properties']['loc']
    #     loc = json_content['features'][i]['properties']['nom_loc']
    #     geometry = json.dumps({'feactures': json_content['features'][i]['geometry']})
    for i in tqdm(range(len(json_content['features']))):
        key_edomunloc = f"{json_content['features'][i]['properties']['entidad']}_{json_content['features'][i]['properties']['mun']}_{json_content['features'][i]['properties']['loc']}"
        id_edo = json_content['features'][i]['properties']['entidad']
        edo = json_content['features'][i]['properties']['nom_ent']
        id_mun = json_content['features'][i]['properties']['mun']
        mun = json_content['features'][i]['properties']['nom_mun']
        id_loc = json_content['features'][i]['properties']['loc']
        loc = json_content['features'][i]['properties']['nom_loc']
        geometry = json.dumps(json_content['features'][i]['geometry'])  # Remove redundant dictionary

        insert_query = "INSERT INTO coordenadas_loc (key_edomunloc, id_edo, edo, id_mun, mun, id_loc, loc, json_data) VALUES (%s, %s, %s, %s, %s, %s, %s, %s);"

        cursor.execute(insert_query, (key_edomunloc, id_edo, edo, id_mun, mun, id_loc, loc, geometry))
        conn.commit()

    # -------


    # Guardar cambios
    
    # Cerrar la conexión
    cursor.close()
    conn.close()
    print(f'Servidor {ip} actualizado en coordenadas de mexico (pais)')


100%|██████████| 192244/192244 [20:23<00:00, 157.09it/s]

Servidor 192.168.1.81 actualizado en coordenadas de mexico (pais)


In [2]:
# dict_keys(['type', 'id', 'geometry', 'geometry_name', 'properties'])

id_edo = json_content['features'][0]['properties']['entidad']
edo = json_content['features'][0]['properties']['nom_ent']
id_mun = json_content['features'][0]['properties']['mun']
mun = json_content['features'][0]['properties']['nom_mun']
id_loc = json_content['features'][0]['properties']['loc']
loc = json_content['features'][0]['properties']['nom_loc']
geometry = json_content['features'][0]['geometry']